In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [ ]:
import os
from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
os.environ["HF_TOKEN"] = user_secrets.get_secret("entire_hf_write_access")

In [ ]:
!pip install -q trackio kagglehub

In [ ]:
# ============================================================================
# SECTION A: ENVIRONMENT & DEPENDENCIES
# ============================================================================

!pip install -q trackio kagglehub

import os
import gc
import numpy as np
import pandas as pd
from PIL import Image
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
import pytorch_lightning as pl
from pytorch_lightning.callbacks import ModelCheckpoint
from sklearn.model_selection import train_test_split
from kaggle_secrets import UserSecretsClient
import trackio
import kagglehub

# ============================================================================
# SECTION B: GLOBAL SETTINGS
# ============================================================================

class PipelineSettings:
    """Manages all static parameters and paths for the project."""
    
    def __init__(self):
        # --- Data Source Paths ---
        self.DATA_ROOT_DIR = "/kaggle/input/sep-25-dl-gen-ai-nppe-1/face_dataset"
        self.TRAIN_CSV_PATH = f"{self.DATA_ROOT_DIR}/train.csv"
        self.TEST_CSV_PATH = f"{self.DATA_ROOT_DIR}/test.csv"
        
        # --- Model Hyperparameters ---
        self.INPUT_IMAGE_SIZE = 128
        self.BATCH_SIZE = 128
        self.LEARNING_RATE = 1e-3
        self.NUM_EPOCHS = 10
        self.AGE_LOSS_WEIGHT = 0.01
        
        # --- Model Architecture Selection ---
        self.SCRATCH_MODEL_ID = "scratch_cnn"
        self.FINETUNED_MODEL_ID = "resnet_finetuned"
        
        # --- System & Environment ---
        self.NUM_DATALOADER_WORKERS = os.cpu_count()
        
        # --- Kaggle Model Upload Settings ---
        self.KAGGLE_USERNAME = None  # Will be fetched automatically
        self.MODEL_NAME = "face-age-gender-predictor"  # Your model name on Kaggle

# Instantiate global settings
settings = PipelineSettings()

# ============================================================================
# SECTION C: IMAGE AUGMENTATION & PREPROCESSING
# ============================================================================

class ImageAugmentor:
    """Defines image transformation pipelines for training and evaluation."""
    
    def __init__(self, image_size):
        self.image_size = image_size
        self.normalization_params = {'mean': [0.485, 0.456, 0.406], 'std': [0.229, 0.224, 0.225]}

    def get_training_transforms(self):
        """Returns an augmented transformation pipeline for the training set."""
        return transforms.Compose([
            transforms.Resize((self.image_size, self.image_size)),
            transforms.RandomHorizontalFlip(p=0.5),
            transforms.ColorJitter(brightness=0.1, contrast=0.1, saturation=0.1),
            transforms.ToTensor(),
            transforms.Normalize(**self.normalization_params),
        ])
    
    def get_inference_transforms(self):
        """Returns a standard transformation pipeline for validation and testing."""
        return transforms.Compose([
            transforms.Resize((self.image_size, self.image_size)),
            transforms.ToTensor(),
            transforms.Normalize(**self.normalization_params),
        ])

# ============================================================================
# SECTION D: CUSTOM DATASET LOADER
# ============================================================================

class FaceImageDataset(Dataset):
    """Custom PyTorch Dataset to load facial images and their attributes."""
    
    def __init__(self, metadata_df, image_dir, image_transform=None, is_prediction=False):
        self.metadata = metadata_df
        self.image_dir = image_dir
        self.transform = image_transform
        self.is_prediction = is_prediction
    
    def __len__(self):
        return len(self.metadata)
    
    def __getitem__(self, idx):
        row = self.metadata.iloc[idx]
        image_path = os.path.join(self.image_dir, row['full_path'])
        image = Image.open(image_path).convert("RGB")
        
        if self.transform:
            image = self.transform(image)
        
        if self.is_prediction:
            return image
        else:
            gender_target = torch.tensor(row['gender'], dtype=torch.float32)
            age_target = torch.tensor(row['age'], dtype=torch.float32)
            return image, gender_target, age_target

# ============================================================================
# SECTION E: PYTORCH LIGHTNING DATA MODULE
# ============================================================================

class FaceDataModule(pl.LightningDataModule):
    """Encapsulates all data loading and splitting logic."""
    
    def __init__(self, config: PipelineSettings):
        super().__init__()
        self.cfg = config
        self.augmentor = ImageAugmentor(self.cfg.INPUT_IMAGE_SIZE)
        self.train_df, self.val_df = None, None

    def prepare_data(self):
        pass

    def setup(self, stage=None):
        if stage == 'fit' or stage is None:
            full_train_data = pd.read_csv(self.cfg.TRAIN_CSV_PATH)
            self.train_df, self.val_df = train_test_split(
                full_train_data, 
                test_size=0.15, 
                random_state=42, 
                stratify=full_train_data['gender']
            )
            
            self.train_dataset = FaceImageDataset(
                self.train_df, 
                self.cfg.DATA_ROOT_DIR,
                self.augmentor.get_training_transforms()
            )
            
            self.val_dataset = FaceImageDataset(
                self.val_df,
                self.cfg.DATA_ROOT_DIR,
                self.augmentor.get_inference_transforms()
            )
    
    def train_dataloader(self):
        return DataLoader(self.train_dataset, batch_size=self.cfg.BATCH_SIZE, shuffle=True, num_workers=self.cfg.NUM_DATALOADER_WORKERS)
    
    def val_dataloader(self):
        return DataLoader(self.val_dataset, batch_size=self.cfg.BATCH_SIZE, num_workers=self.cfg.NUM_DATALOADER_WORKERS)

# ============================================================================
# SECTION F: ABSTRACT MODEL DEFINITION
# ============================================================================

class AbstractFaceModel(pl.LightningModule):
    """A base class for face attribute models, defining the training loop and loss."""
    
    def __init__(self, learning_rate, age_loss_weight):
        super().__init__()
        self.save_hyperparameters()
        self.lr = learning_rate
        self.age_weight = age_loss_weight
        self.gender_loss_fn = nn.BCEWithLogitsLoss()
        self.age_loss_fn = nn.MSELoss()

    def _calculate_combined_loss(self, gender_preds, age_preds, gender_labels, age_labels):
        gender_loss = self.gender_loss_fn(gender_preds.squeeze(), gender_labels)
        age_loss = self.age_loss_fn(age_preds.squeeze(), age_labels)
        total_loss = gender_loss + (age_loss * self.age_weight)
        return total_loss

    def training_step(self, batch, batch_idx):
        images, gender_labels, age_labels = batch
        gender_preds, age_preds = self(images)
        loss = self._calculate_combined_loss(gender_preds, age_preds, gender_labels, age_labels)
        self.log('train_loss', loss, on_step=True, on_epoch=True, prog_bar=True)
        return loss
    
    def validation_step(self, batch, batch_idx):
        images, gender_labels, age_labels = batch
        gender_preds, age_preds = self(images)
        loss = self._calculate_combined_loss(gender_preds, age_preds, gender_labels, age_labels)
        self.log('val_loss', loss, on_epoch=True, prog_bar=True)
    
    def configure_optimizers(self):
        optimizer = torch.optim.Adam(self.parameters(), lr=self.lr)
        return optimizer

# ============================================================================
# SECTION G: CUSTOM SCRATCH CNN MODEL
# ============================================================================

class ScratchCNNModel(AbstractFaceModel):
    """A custom Convolutional Neural Network built from scratch."""
    
    def __init__(self, learning_rate, age_loss_weight):
        super().__init__(learning_rate, age_loss_weight)
        
        def conv_block(in_f, out_f):
            return nn.Sequential(
                nn.Conv2d(in_f, out_f, kernel_size=3, padding=1, bias=False),
                nn.BatchNorm2d(out_f),
                nn.ReLU(inplace=True),
                nn.MaxPool2d(kernel_size=2, stride=2)
            )

        self.feature_extractor = nn.Sequential(
            conv_block(3, 32),
            conv_block(32, 64),
            conv_block(64, 128),
            conv_block(128, 256),
        )
        
        probe_tensor = torch.randn(1, 3, settings.INPUT_IMAGE_SIZE, settings.INPUT_IMAGE_SIZE)
        flattened_size = self.feature_extractor(probe_tensor).view(1, -1).size(1)
        
        self.gender_head = nn.Linear(flattened_size, 1)
        self.age_head = nn.Linear(flattened_size, 1)

    def forward(self, x):
        features = self.feature_extractor(x)
        features = torch.flatten(features, 1)
        gender_output = self.gender_head(features)
        age_output = self.age_head(features)
        return gender_output, age_output

# ============================================================================
# SECTION H: TRANSFER LEARNING MODEL (ResNet18)
# ============================================================================

class FineTunedResNetModel(AbstractFaceModel):
    """A model using a pre-trained ResNet18 backbone for feature extraction."""
    
    def __init__(self, learning_rate, age_loss_weight):
        super().__init__(learning_rate, age_loss_weight)
        resnet = models.resnet18(weights=models.ResNet18_Weights.DEFAULT)
        num_features = resnet.fc.in_features
        
        self.backbone = nn.Sequential(*list(resnet.children())[:-1])
        
        self.gender_head = nn.Linear(num_features, 1)
        self.age_head = nn.Linear(num_features, 1)

    def forward(self, x):
        features = self.backbone(x)
        features = torch.flatten(features, 1)
        gender_output = self.gender_head(features)
        age_output = self.age_head(features)
        return gender_output, age_output

# ============================================================================
# SECTION I: EXECUTION & ORCHESTRATION
# ============================================================================

class PipelineRunner:
    """Coordinates training and model upload workflow."""
    
    def __init__(self, cfg: PipelineSettings):
        self.cfg = cfg
        self.data_module = FaceDataModule(cfg)
        self._authenticate_trackio()
        self._get_kaggle_username()

    def _authenticate_trackio(self):
        try:
            secrets = UserSecretsClient()
            hf_token = secrets.get_secret("HUGGINGFACE_TOKEN")  # Store in Kaggle Secrets
            os.environ["HF_TOKEN"] = hf_token
            print("→ TrackIO authentication configured.")
        except Exception as e:
            print(f"⚠ Could not configure TrackIO authentication: {e}")

    def _get_kaggle_username(self):
        """Fetch Kaggle username for model upload."""
        try:
            user_info = kagglehub.whoami()
            self.cfg.KAGGLE_USERNAME = user_info['username']
            print(f"→ Kaggle username: {self.cfg.KAGGLE_USERNAME}")
        except Exception as e:
            print(f"⚠ Could not fetch Kaggle username: {e}")
            self.cfg.KAGGLE_USERNAME = "your-username"  # Fallback

    def _run_training_session(self, model_instance, model_name, tracking_id):
        print(f"\n{'='*70}\n🚀 Starting Training: {model_name}\n{'='*70}")
        
        trackio.init(
            project="25-t3-nppe1",
            name=tracking_id,
            config={
                "space_id": "josondev/IITM-NPPE",
                "learning_rate": self.cfg.LEARNING_RATE,
                "epochs": self.cfg.NUM_EPOCHS,
                "model_type": model_name
            }
        )
        
        checkpoint_cb = ModelCheckpoint(
            monitor='val_loss',
            dirpath='/kaggle/working/',
            filename=f'{model_name}-best-model',
            save_top_k=1,
            mode='min'
        )
        
        trainer = pl.Trainer(
            max_epochs=self.cfg.NUM_EPOCHS,
            accelerator='gpu',
            devices='auto',
            strategy="ddp_notebook",
            callbacks=[checkpoint_cb]
        )
        
        trainer.fit(model_instance, self.data_module)
        print(f"✅ Best checkpoint saved at: {checkpoint_cb.best_model_path}")
        
        final_val_loss = trainer.callback_metrics.get('val_loss', torch.tensor(0.0)).item()
        trackio.log({"final_validation_loss": final_val_loss})
        trackio.finish()
        
        # Upload to Kaggle Hub
        self._upload_to_kaggle_hub(checkpoint_cb.best_model_path, model_name, final_val_loss)
        
        del model_instance, trainer, checkpoint_cb
        gc.collect()
        torch.cuda.empty_cache()

    def _upload_to_kaggle_hub(self, checkpoint_path, model_name, val_loss):
        """Upload trained checkpoint to Kaggle Models."""
        print(f"\n{'='*70}\n📤 Uploading {model_name} to Kaggle Hub...\n{'='*70}")
        
        try:
            # Define handle: username/model/framework/variation
            framework = "pyTorch"
            variation = model_name.replace("_", "-")  # e.g., "scratch-cnn" or "resnet-finetuned"
            handle = f"{self.cfg.KAGGLE_USERNAME}/{self.cfg.MODEL_NAME}/{framework}/{variation}"
            
            # Create a directory with checkpoint and metadata
            upload_dir = f"/kaggle/working/{model_name}_upload"
            os.makedirs(upload_dir, exist_ok=True)
            
            # Copy checkpoint
            import shutil
            shutil.copy(checkpoint_path, os.path.join(upload_dir, "model.ckpt"))
            
            # Create a README (optional but recommended)
            with open(os.path.join(upload_dir, "README.md"), "w") as f:
                f.write(f"# {model_name.replace('_', ' ').title()} Model\n\n")
                f.write(f"**Validation Loss:** {val_loss:.4f}\n\n")
                f.write(f"**Framework:** PyTorch Lightning\n\n")
                f.write(f"**Task:** Gender classification (binary) + Age regression\n\n")
                f.write(f"Trained on face dataset with {self.cfg.NUM_EPOCHS} epochs.\n")
            
            # Upload using kagglehub
            version_notes = f"Val loss: {val_loss:.4f}, Epochs: {self.cfg.NUM_EPOCHS}"
            kagglehub.model_upload(
                handle=handle,
                local_model_dir=upload_dir,
                version_notes=version_notes,
                license_name="Apache 2.0"
            )
            
            print(f"✅ Model uploaded successfully!")
            print(f"   View at: https://www.kaggle.com/models/{self.cfg.KAGGLE_USERNAME}/{self.cfg.MODEL_NAME}/{framework}/{variation}")
            
        except Exception as e:
            print(f"⚠ Upload failed: {e}")
            print("   You can manually upload from /kaggle/working/ via Kaggle UI or dataset creation.")

    def execute(self):
        """Main entry point: Training only (no inference)."""
        print("\n*** MODE: TRAINING + UPLOAD ***")
        
        # Train Scratch Model
        scratch_model = ScratchCNNModel(self.cfg.LEARNING_RATE, self.cfg.AGE_LOSS_WEIGHT)
        self._run_training_session(scratch_model, "scratch_cnn", "BaselineCNN-v2")

        # Train Finetuned Model
        finetuned_model = FineTunedResNetModel(self.cfg.LEARNING_RATE, self.cfg.AGE_LOSS_WEIGHT)
        self._run_training_session(finetuned_model, "resnet_finetuned", "TransferResNet-v2")
        
        print("\n🎉 Training and upload pipeline completed!")
        print("   Both models are now available on Kaggle Models for inference.")

# ============================================================================
# SECTION J: SCRIPT EXECUTION
# ============================================================================

if __name__ == "__main__":
    pipeline = PipelineRunner(settings)
    pipeline.execute()


In [ ]:
!ls -lh /kaggle/working | grep -i submission

In [15]:
# ============================================================================
# INFERENCE NOTEBOOK: Download Models from Kaggle Hub & Generate Submissions
# ============================================================================
# This notebook loads pre-trained models from Kaggle Models and creates
# submission_scratch.csv and submission_finetuned.csv for competition upload.

!pip install -q kagglehub

import os
import gc
import numpy as np
import pandas as pd
from PIL import Image
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
import pytorch_lightning as pl
import kagglehub

# ============================================================================
# SECTION A: SETTINGS & PATHS
# ============================================================================

class InferenceSettings:
    """Configuration for inference pipeline."""
    
    def __init__(self):
        # Data paths
        self.DATA_ROOT_DIR = "/kaggle/input/sep-25-dl-gen-ai-nppe-1/face_dataset"
        self.TEST_CSV_PATH = f"{self.DATA_ROOT_DIR}/test.csv"
        
        # Model parameters (must match training)
        self.INPUT_IMAGE_SIZE = 128
        self.BATCH_SIZE = 128
        self.LEARNING_RATE = 1e-3
        self.AGE_LOSS_WEIGHT = 0.01
        
        # Kaggle Model Hub handles (UPDATE with your username)
        self.KAGGLE_USERNAME = "rexjosondeva"  # Replace with your Kaggle username
        self.MODEL_NAME = "face-age-gender-predictor"
        self.SCRATCH_HANDLE = f"{self.KAGGLE_USERNAME}/{self.MODEL_NAME}/pyTorch/scratch-cnn"
        self.FINETUNED_HANDLE = f"{self.KAGGLE_USERNAME}/{self.MODEL_NAME}/pyTorch/resnet-finetuned"
        
        # System
        self.NUM_WORKERS = 2  # Reduce for stability

settings = InferenceSettings()

# ============================================================================
# SECTION B: DATA LOADING
# ============================================================================

class ImageAugmentor:
    """Inference-time image transforms (no augmentation)."""
    def __init__(self, image_size=128):
        self.transform = transforms.Compose([
            transforms.Resize((image_size, image_size)),
            transforms.ToTensor(),
            transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
        ])

class FaceImageTestDataset(Dataset):
    """Test dataset loader."""
    def __init__(self, metadata_df, image_dir, transform=None):
        self.metadata = metadata_df
        self.image_dir = image_dir
        self.transform = transform
    
    def __len__(self):
        return len(self.metadata)
    
    def __getitem__(self, idx):
        row = self.metadata.iloc[idx]
        image_path = os.path.join(self.image_dir, row['full_path'])
        image = Image.open(image_path).convert("RGB")
        if self.transform:
            image = self.transform(image)
        return image

# Load test data
test_df = pd.read_csv(settings.TEST_CSV_PATH)
augmentor = ImageAugmentor(settings.INPUT_IMAGE_SIZE)
test_dataset = FaceImageTestDataset(test_df, settings.DATA_ROOT_DIR, augmentor.transform)
test_loader = DataLoader(test_dataset, batch_size=settings.BATCH_SIZE, shuffle=False, num_workers=settings.NUM_WORKERS)

print(f"✅ Test dataset loaded: {len(test_df)} samples")

# ============================================================================
# SECTION C: MODEL DEFINITIONS (Must Match Training)
# ============================================================================

class ScratchCNNModel(pl.LightningModule):
    """Custom CNN from scratch."""
    def __init__(self, learning_rate, age_loss_weight):
        super().__init__()
        self.save_hyperparameters()
        
        def conv_block(in_f, out_f):
            return nn.Sequential(
                nn.Conv2d(in_f, out_f, kernel_size=3, padding=1, bias=False),
                nn.BatchNorm2d(out_f),
                nn.ReLU(inplace=True),
                nn.MaxPool2d(kernel_size=2, stride=2)
            )
        
        self.feature_extractor = nn.Sequential(
            conv_block(3, 32),
            conv_block(32, 64),
            conv_block(64, 128),
            conv_block(128, 256),
        )
        
        probe = torch.randn(1, 3, 128, 128)
        flat_size = self.feature_extractor(probe).view(1, -1).size(1)
        self.gender_head = nn.Linear(flat_size, 1)
        self.age_head = nn.Linear(flat_size, 1)
    
    def forward(self, x):
        features = self.feature_extractor(x)
        features = torch.flatten(features, 1)
        return self.gender_head(features), self.age_head(features)

class FineTunedResNetModel(pl.LightningModule):
    """Fine-tuned ResNet18 model."""
    def __init__(self, learning_rate, age_loss_weight):
        super().__init__()
        self.save_hyperparameters()
        resnet = models.resnet18(weights=models.ResNet18_Weights.DEFAULT)
        num_features = resnet.fc.in_features
        self.backbone = nn.Sequential(*list(resnet.children())[:-1])
        self.gender_head = nn.Linear(num_features, 1)
        self.age_head = nn.Linear(num_features, 1)
    
    def forward(self, x):
        features = self.backbone(x)
        features = torch.flatten(features, 1)
        return self.gender_head(features), self.age_head(features)

# ============================================================================
# SECTION D: DOWNLOAD MODELS FROM KAGGLE HUB
# ============================================================================

print("\n" + "="*70)
print("📥 Downloading Models from Kaggle Hub...")
print("="*70)

# Download scratch model
print(f"\n→ Downloading Scratch CNN from: {settings.SCRATCH_HANDLE}")
scratch_model_dir = kagglehub.model_download(settings.SCRATCH_HANDLE)
scratch_ckpt_path = os.path.join(scratch_model_dir, "model.ckpt")
print(f"   ✅ Downloaded to: {scratch_ckpt_path}")

# Download finetuned model
print(f"\n→ Downloading Fine-Tuned ResNet from: {settings.FINETUNED_HANDLE}")
finetuned_model_dir = kagglehub.model_download(settings.FINETUNED_HANDLE)
finetuned_ckpt_path = os.path.join(finetuned_model_dir, "model.ckpt")
print(f"   ✅ Downloaded to: {finetuned_ckpt_path}")

# Verify files exist
assert os.path.exists(scratch_ckpt_path), f"Scratch checkpoint not found: {scratch_ckpt_path}"
assert os.path.exists(finetuned_ckpt_path), f"Finetuned checkpoint not found: {finetuned_ckpt_path}"

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"\n✅ Using device: {device}")

# ============================================================================
# SECTION E: INFERENCE - SCRATCH MODEL
# ============================================================================

print("\n" + "="*70)
print("🔮 Running Scratch CNN Predictions...")
print("="*70)

scratch_model = ScratchCNNModel.load_from_checkpoint(
    checkpoint_path=scratch_ckpt_path,
    learning_rate=settings.LEARNING_RATE,
    age_loss_weight=settings.AGE_LOSS_WEIGHT
)
scratch_model.eval()
scratch_model.to(device)

scratch_gender_logits, scratch_age_outputs = [], []
with torch.no_grad():
    for images in test_loader:
        images = images.to(device)
        gender_pred, age_pred = scratch_model(images)
        scratch_gender_logits.append(gender_pred.cpu())
        scratch_age_outputs.append(age_pred.cpu())

# Post-process predictions
scratch_gender_logits = torch.cat(scratch_gender_logits).numpy().reshape(-1)
scratch_age_outputs = torch.cat(scratch_age_outputs).numpy().reshape(-1)
scratch_gender_probs = 1 / (1 + np.exp(-scratch_gender_logits))
scratch_gender_preds = (scratch_gender_probs > 0.5).astype(int)
scratch_age_preds = np.clip(scratch_age_outputs, 0, 120)

# Save submission
submission_scratch = pd.DataFrame({
    'id': test_df['id'].values,
    'gender': scratch_gender_preds,
    'age': scratch_age_preds
})
submission_scratch.to_csv('/kaggle/working/submission_scratch.csv', index=False)

print("✅ Scratch CNN submission saved: submission_scratch.csv")
print(submission_scratch.head())
print(f"Shape: {submission_scratch.shape}")

# Free memory
del scratch_model, scratch_gender_logits, scratch_age_outputs
gc.collect()
torch.cuda.empty_cache()

# ============================================================================
# SECTION F: INFERENCE - FINETUNED MODEL
# ============================================================================

print("\n" + "="*70)
print("🔮 Running Fine-Tuned ResNet Predictions...")
print("="*70)

finetuned_model = FineTunedResNetModel.load_from_checkpoint(
    checkpoint_path=finetuned_ckpt_path,
    learning_rate=settings.LEARNING_RATE,
    age_loss_weight=settings.AGE_LOSS_WEIGHT
)
finetuned_model.eval()
finetuned_model.to(device)

finetuned_gender_logits, finetuned_age_outputs = [], []
with torch.no_grad():
    for images in test_loader:
        images = images.to(device)
        gender_pred, age_pred = finetuned_model(images)
        finetuned_gender_logits.append(gender_pred.cpu())
        finetuned_age_outputs.append(age_pred.cpu())

# Post-process predictions
finetuned_gender_logits = torch.cat(finetuned_gender_logits).numpy().reshape(-1)
finetuned_age_outputs = torch.cat(finetuned_age_outputs).numpy().reshape(-1)
finetuned_gender_probs = 1 / (1 + np.exp(-finetuned_gender_logits))
finetuned_gender_preds = (finetuned_gender_probs > 0.5).astype(int)
finetuned_age_preds = np.clip(finetuned_age_outputs, 0, 120)

# Save submission
submission_finetuned = pd.DataFrame({
    'id': test_df['id'].values,
    'gender': finetuned_gender_preds,
    'age': finetuned_age_preds
})
submission_finetuned.to_csv('/kaggle/working/submission_finetuned.csv', index=False)

print("✅ Fine-Tuned ResNet submission saved: submission_finetuned.csv")
print(submission_finetuned.head())
print(f"Shape: {submission_finetuned.shape}")

# Free memory
del finetuned_model, finetuned_gender_logits, finetuned_age_outputs
gc.collect()
torch.cuda.empty_cache()

# ============================================================================
# SECTION G: OPTIONAL ENSEMBLE
# ============================================================================

print("\n" + "="*70)
print("🎯 Generating Ensemble Submission (Average of Both Models)...")
print("="*70)

ensemble_gender = ((scratch_gender_preds + finetuned_gender_preds) / 2 > 0.5).astype(int)
ensemble_age = (scratch_age_preds + finetuned_age_preds) / 2

submission_ensemble = pd.DataFrame({
    'id': test_df['id'].values,
    'gender': ensemble_gender,
    'age': ensemble_age
})
submission_ensemble.to_csv('/kaggle/working/submission_ensemble.csv', index=False)

print("✅ Ensemble submission saved: submission_ensemble.csv")
print(submission_ensemble.head())
print(f"Shape: {submission_ensemble.shape}")

# ============================================================================
# FINAL SUMMARY
# ============================================================================

print("\n" + "="*70)
print("🎉 ALL SUBMISSIONS GENERATED SUCCESSFULLY!")
print("="*70)
print("Files in /kaggle/working/:")
print("  - submission_scratch.csv")
print("  - submission_finetuned.csv")
print("  - submission_ensemble.csv")
print("\nDownload from Output panel and submit to competition!")
print("="*70)


✅ Test dataset loaded: 8677 samples

📥 Downloading Models from Kaggle Hub...

→ Downloading Scratch CNN from: rexjosondeva/face-age-gender-predictor/pyTorch/scratch-cnn
Mounting files to /kaggle/input/face-age-gender-predictor/pytorch/scratch-cnn/2...
   ✅ Downloaded to: /kaggle/input/face-age-gender-predictor/pytorch/scratch-cnn/2/model.ckpt

→ Downloading Fine-Tuned ResNet from: rexjosondeva/face-age-gender-predictor/pyTorch/resnet-finetuned
   ✅ Downloaded to: /kaggle/input/face-age-gender-predictor/pytorch/resnet-finetuned/2/model.ckpt

✅ Using device: cuda

🔮 Running Scratch CNN Predictions...
✅ Scratch CNN submission saved: submission_scratch.csv
   id  gender        age
0   0       1  30.513975
1   1       0  22.544374
2   2       1  29.283455
3   3       1  29.424118
4   4       1  51.745323
Shape: (8677, 3)

🔮 Running Fine-Tuned ResNet Predictions...
✅ Fine-Tuned ResNet submission saved: submission_finetuned.csv
   id  gender        age
0   0       1  35.028824
1   1       0  

In [16]:
# ============================================================================
# SCRATCH CNN INFERENCE (Fixed Layer Names)
# ============================================================================

import os
import gc
import numpy as np
import pandas as pd
from PIL import Image
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
import pytorch_lightning as pl

# Settings
class Config:
    DATA_ROOT = "/kaggle/input/sep-25-dl-gen-ai-nppe-1/face_dataset"
    TEST_CSV = f"{DATA_ROOT}/test.csv"
    IMG_SIZE = 128
    BATCH = 128
    LR = 1e-3
    AGE_WEIGHT = 0.01
    WORKERS = 2

cfg = Config()

# Auto-detect checkpoint
print("="*70)
print("🔍 Searching for scratch model checkpoint...")
print("="*70)

cfg.CHECKPOINT = None
for root, dirs, files in os.walk("/kaggle/input/"):
    for file in files:
        if file == "model.ckpt" and "scratch" in root.lower():
            cfg.CHECKPOINT = os.path.join(root, file)
            print(f"✅ Found: {cfg.CHECKPOINT}")
            break
    if cfg.CHECKPOINT:
        break

if cfg.CHECKPOINT is None:
    raise FileNotFoundError("Add Kaggle Model: face-age-gender-predictor (scratch-cnn) via 'Add Input'")

# Data Pipeline
class ImageTransform:
    def __init__(self, size=128):
        self.transform = transforms.Compose([
            transforms.Resize((size, size)),
            transforms.ToTensor(),
            transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
        ])

class TestDataset(Dataset):
    def __init__(self, df, root, tfm):
        self.df, self.root, self.tfm = df, root, tfm
    def __len__(self): return len(self.df)
    def __getitem__(self, i):
        img = Image.open(os.path.join(self.root, self.df.iloc[i]['full_path'])).convert("RGB")
        return self.tfm(img)

test_df = pd.read_csv(cfg.TEST_CSV)
test_ds = TestDataset(test_df, cfg.DATA_ROOT, ImageTransform(cfg.IMG_SIZE).transform)
test_dl = DataLoader(test_ds, batch_size=cfg.BATCH, shuffle=False, num_workers=cfg.WORKERS)
print(f"✅ Test: {len(test_df)} samples")

# Model (FIXED: Match training architecture with "feature_extractor")
class ScratchCNN(pl.LightningModule):
    def __init__(self, lr, age_w):
        super().__init__()
        self.save_hyperparameters()
        
        def conv_block(in_c, out_c):
            return nn.Sequential(
                nn.Conv2d(in_c, out_c, 3, padding=1, bias=False),
                nn.BatchNorm2d(out_c),
                nn.ReLU(inplace=True),
                nn.MaxPool2d(2, 2)
            )
        
        # MUST be named "feature_extractor" to match checkpoint
        self.feature_extractor = nn.Sequential(
            conv_block(3, 32),
            conv_block(32, 64),
            conv_block(64, 128),
            conv_block(128, 256),
        )
        
        probe = torch.randn(1, 3, 128, 128)
        flat_size = self.feature_extractor(probe).view(1, -1).size(1)
        self.gender_head = nn.Linear(flat_size, 1)
        self.age_head = nn.Linear(flat_size, 1)
    
    def forward(self, x):
        features = torch.flatten(self.feature_extractor(x), 1)
        return self.gender_head(features), self.age_head(features)

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"✅ Device: {device}\n")

# Inference
print("="*70)
print("🔮 Scratch CNN Predictions...")
print("="*70)

model = ScratchCNN.load_from_checkpoint(cfg.CHECKPOINT, lr=cfg.LR, age_w=cfg.AGE_WEIGHT)
model.eval().to(device)

g_logits, a_outputs = [], []
with torch.no_grad():
    for imgs in test_dl:
        g, a = model(imgs.to(device))
        g_logits.append(g.cpu())
        a_outputs.append(a.cpu())

g_logits = torch.cat(g_logits).numpy().flatten()
a_outputs = torch.cat(a_outputs).numpy().flatten()
g_probs = 1 / (1 + np.exp(-g_logits))
g_preds = (g_probs > 0.5).astype(int)
a_preds = np.clip(a_outputs, 0, 120)

submission = pd.DataFrame({'id': test_df['id'], 'gender': g_preds, 'age': a_preds})
submission.to_csv('/kaggle/working/submission.csv', index=False)

print("✅ submission.csv (Scratch CNN)")
print(submission.head())
print(f"Shape: {submission.shape}")
print("\n🎉 Ready for submission!")

del model; gc.collect(); torch.cuda.empty_cache()


🔍 Searching for scratch model checkpoint...
✅ Found: /kaggle/input/face-age-gender-predictor/pytorch/scratch-cnn/1/model.ckpt
✅ Test: 8677 samples
✅ Device: cuda

🔮 Scratch CNN Predictions...
✅ submission.csv (Scratch CNN)
   id  gender        age
0   0       1  33.268768
1   1       0  24.642073
2   2       1  34.242413
3   3       1  27.935734
4   4       1  50.617668
Shape: (8677, 3)

🎉 Ready for submission!


In [17]:
# ============================================================================
# FINE-TUNED RESNET INFERENCE (Fixed Layer Names)
# ============================================================================

import os
import gc
import numpy as np
import pandas as pd
from PIL import Image
import torch
from torch import nn
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, models
import pytorch_lightning as pl

# Settings
class Config:
    DATA_ROOT = "/kaggle/input/sep-25-dl-gen-ai-nppe-1/face_dataset"
    TEST_CSV = f"{DATA_ROOT}/test.csv"
    IMG_SIZE = 128
    BATCH = 128
    LR = 1e-3
    AGE_WEIGHT = 0.01
    WORKERS = 2

cfg = Config()

# Auto-detect checkpoint
print("="*70)
print("🔍 Searching for finetuned model checkpoint...")
print("="*70)

cfg.CHECKPOINT = None
for root, dirs, files in os.walk("/kaggle/input/"):
    for file in files:
        if file == "model.ckpt" and ("resnet" in root.lower() or "finetuned" in root.lower() or "finetune" in root.lower()):
            cfg.CHECKPOINT = os.path.join(root, file)
            print(f"✅ Found: {cfg.CHECKPOINT}")
            break
    if cfg.CHECKPOINT:
        break

if cfg.CHECKPOINT is None:
    raise FileNotFoundError("Add Kaggle Model: face-age-gender-predictor (resnet-finetuned) via 'Add Input'")

# Data Pipeline
class ImageTransform:
    def __init__(self, size=128):
        self.transform = transforms.Compose([
            transforms.Resize((size, size)),
            transforms.ToTensor(),
            transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
        ])

class TestDataset(Dataset):
    def __init__(self, df, root, tfm):
        self.df, self.root, self.tfm = df, root, tfm
    def __len__(self): return len(self.df)
    def __getitem__(self, i):
        img = Image.open(os.path.join(self.root, self.df.iloc[i]['full_path'])).convert("RGB")
        return self.tfm(img)

test_df = pd.read_csv(cfg.TEST_CSV)
test_ds = TestDataset(test_df, cfg.DATA_ROOT, ImageTransform(cfg.IMG_SIZE).transform)
test_dl = DataLoader(test_ds, batch_size=cfg.BATCH, shuffle=False, num_workers=cfg.WORKERS)
print(f"✅ Test: {len(test_df)} samples")

# Model (Match training architecture exactly)
class FineTunedResNet(pl.LightningModule):
    def __init__(self, lr, age_w):
        super().__init__()
        self.save_hyperparameters()
        resnet = models.resnet18(weights=models.ResNet18_Weights.DEFAULT)
        num_features = resnet.fc.in_features
        self.backbone = nn.Sequential(*list(resnet.children())[:-1])
        self.gender_head = nn.Linear(num_features, 1)
        self.age_head = nn.Linear(num_features, 1)
    
    def forward(self, x):
        features = torch.flatten(self.backbone(x), 1)
        return self.gender_head(features), self.age_head(features)

device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"✅ Device: {device}\n")

# Inference
print("="*70)
print("🔮 Fine-Tuned ResNet Predictions...")
print("="*70)

model = FineTunedResNet.load_from_checkpoint(cfg.CHECKPOINT, lr=cfg.LR, age_w=cfg.AGE_WEIGHT)
model.eval().to(device)

g_logits, a_outputs = [], []
with torch.no_grad():
    for imgs in test_dl:
        g, a = model(imgs.to(device))
        g_logits.append(g.cpu())
        a_outputs.append(a.cpu())

g_logits = torch.cat(g_logits).numpy().flatten()
a_outputs = torch.cat(a_outputs).numpy().flatten()
g_probs = 1 / (1 + np.exp(-g_logits))
g_preds = (g_probs > 0.5).astype(int)
a_preds = np.clip(a_outputs, 0, 120)

submission = pd.DataFrame({'id': test_df['id'], 'gender': g_preds, 'age': a_preds})
submission.to_csv('/kaggle/working/submission.csv', index=False)

print("✅ submission.csv (Fine-Tuned ResNet)")
print(submission.head())
print(f"Shape: {submission.shape}")
print("\n🎉 Ready for submission!")

del model; gc.collect(); torch.cuda.empty_cache()


🔍 Searching for finetuned model checkpoint...
✅ Found: /kaggle/input/face-age-gender-predictor/pytorch/resnet-finetuned/1/model.ckpt
✅ Test: 8677 samples
✅ Device: cuda

🔮 Fine-Tuned ResNet Predictions...
✅ submission.csv (Fine-Tuned ResNet)
   id  gender        age
0   0       1  33.796421
1   1       0  27.736071
2   2       1  35.373379
3   3       1  24.109423
4   4       1  64.067947
Shape: (8677, 3)

🎉 Ready for submission!
